In [1]:
import os.path
import pandas as pd
import glob

import spacy
nlp = spacy.load("pt_core_news_sm")

from gensim import corpora
from gensim import models

import nltk
from nltk.tokenize import WordPunctTokenizer
from nltk.corpus import stopwords
from nltk.stem.snowball import PortugueseStemmer

import string
from string import punctuation

from collections import defaultdict

from whoosh.index import create_in, open_dir
from whoosh.fields import *
from whoosh.analysis import LanguageAnalyzer
from whoosh.qparser import QueryParser

Verificamos quantos arquivos há no corpus.

In [2]:
caminho = "CE-DOHS/*.txt"
arquivos  = glob.glob(caminho)
len(arquivos)

2370

### Importação dos documentos

In [3]:
cartas = pd.read_csv('cartas.csv')
#cartas.data = pd.to_datetime(cartas.data, format='%Y-%m-%d')
cartas.head()

id  de  para  data  \
0    01-AAD-17-04-1962-mod.txt NaN   NaN   NaN   
1   01-AAD-17-04-1962-orig.txt NaN   NaN   NaN   
2   01-ACST-14-01-1952-mod.txt NaN   NaN   NaN   
3  01-ACST-14-01-1952-orig.txt NaN   NaN   NaN   
4    01-AFS-28-04-1956-mod.txt NaN   NaN   NaN   

                                               texto  
0  NULL\nNULL\nNULL\nNULL\nNULL\nNULL\nNULL\nNULL...  
1  NULL\nNULL\nNULL\nNULL\nNULL\nNULL\nNULL\nNULL...  
2  NULL\nNULL\nNULL\nNULL\nNULL\nNULL\nNULL\nNULL...  
3  NULL\nNULL\nNULL\nNULL\nNULL\nNULL\nNULL\nNULL...  
4  NULL\nNULL\nNULL\nNULL\nNULL\nNULL\nNULL\nNULL...

## Usando os módulos spaCy e gensim

O spaCy tokeniza cada documento e guarda informações sobre cada token.

In [6]:
texto_spacy = []
for i in cartas.index:
    texto_spacy.append([t.text for t in nlp(cartas.texto[i]) if (not t.is_stop) and t.text.strip().strip(punctuation)])

In [7]:
texto_spacy[0]

['Paulo',
 '17',
 'abril',
 '1962',
 'Inesquicível',
 'Lurdes',
 'a',
 'o',
 'tristonho',
 'cheio',
 'saudade',
 'peguei',
 'rude',
 'caneta',
 'escrever',
 'dando',
 'notícias',
 '1',
 'saúde',
 'vou',
 'o',
 'mata',
 '2',
 'a',
 'cruel',
 '3',
 'lembrança',
 'acredite',
 'amor',
 'chega',
 '4',
 'o',
 'domingo',
 'fico',
 'impressão',
 'a',
 'vou',
 'e',
 'a',
 'inda',
 'aumenta',
 'o',
 'sofrer',
 'arrependido',
 'hora',
 'ausentei',
 'sabia',
 'suportava',
 'viver',
 'ausente',
 'amor',
 'sofrer',
 'parece-me',
 'a',
 'única',
 'pessoa',
 'Deus',
 'deixou',
 'amar',
 'amor',
 'jovem',
 'coração',
 'encerra',
 'abraços',
 'fortes',
 'e',
 'aceite',
 'recordações',
 'd',
 'ama',
 'falsidade',
 'o',
 'amor',
 'Arnaldo',
 'Andrade',
 'Dias']

O gensim recebe a lista de tokens de cada document, cria um [dicionário](https://radimrehurek.com/gensim/corpora/dictionary.html) mapeando cada token a um número (objeto dicionario), e cria um 'bag of words', que estamos guardando no objeto corpus (https://www.machinelearningplus.com/nlp/gensim-tutorial/).

In [8]:
dicionario = corpora.Dictionary(doc for doc in texto_spacy)
corpus = [dicionario.doc2bow(doc) for doc in texto_spacy]

In [9]:
dicionario.num_docs

2370

In [10]:
dicionario.id2token

{}

In [11]:
dicionario.cfs

{12: 165,
 1: 191,
 15: 62,
 2: 6,
 10: 1,
 11: 6,
 13: 19424,
 47: 16278,
 58: 4,
 27: 44,
 54: 120,
 49: 12,
 52: 5,
 25: 39,
 36: 259,
 31: 131,
 46: 206,
 0: 1215,
 55: 456,
 60: 710,
 45: 4,
 3: 1189,
 29: 19,
 4: 805,
 44: 248,
 17: 5,
 20: 203,
 26: 40,
 5: 577,
 33: 71,
 38: 112,
 41: 56,
 34: 17610,
 42: 39,
 22: 12,
 56: 26,
 21: 1,
 40: 162,
 24: 2,
 53: 57,
 57: 3,
 59: 70,
 23: 19,
 48: 28,
 61: 27,
 50: 200,
 8: 818,
 32: 77,
 19: 29,
 43: 35,
 28: 231,
 35: 1,
 14: 162,
 39: 21,
 16: 95,
 51: 15,
 30: 2461,
 18: 55,
 37: 5,
 7: 51,
 6: 121,
 9: 116,
 62: 130,
 63: 1,
 72: 1,
 71: 169,
 64: 2,
 65: 1,
 68: 1,
 67: 1,
 73: 1,
 66: 1,
 74: 18,
 69: 1,
 70: 1,
 91: 204,
 93: 55,
 75: 217,
 165: 1261,
 77: 24,
 144: 111,
 136: 32,
 94: 469,
 87: 2,
 130: 48,
 166: 881,
 82: 2,
 167: 835,
 164: 277,
 153: 54,
 85: 2,
 84: 2,
 141: 207,
 149: 340,
 107: 17,
 86: 495,
 132: 822,
 150: 357,
 145: 37,
 147: 95,
 134: 5,
 104: 1,
 154: 3,
 156: 5,
 162: 8,
 157: 122,
 112: 22,
 119

In [12]:
corpus[0] # Primeiro documento

[(0, 1),
 (1, 1),
 (2, 1),
 (3, 1),
 (4, 1),
 (5, 1),
 (6, 1),
 (7, 1),
 (8, 1),
 (9, 1),
 (10, 1),
 (11, 1),
 (12, 1),
 (13, 5),
 (14, 1),
 (15, 1),
 (16, 1),
 (17, 1),
 (18, 1),
 (19, 1),
 (20, 4),
 (21, 1),
 (22, 1),
 (23, 1),
 (24, 1),
 (25, 1),
 (26, 1),
 (27, 1),
 (28, 1),
 (29, 1),
 (30, 1),
 (31, 1),
 (32, 1),
 (33, 1),
 (34, 2),
 (35, 1),
 (36, 1),
 (37, 1),
 (38, 1),
 (39, 1),
 (40, 1),
 (41, 1),
 (42, 1),
 (43, 1),
 (44, 1),
 (45, 1),
 (46, 1),
 (47, 5),
 (48, 1),
 (49, 1),
 (50, 1),
 (51, 1),
 (52, 1),
 (53, 1),
 (54, 1),
 (55, 1),
 (56, 2),
 (57, 1),
 (58, 1),
 (59, 1),
 (60, 2),
 (61, 1)]

Gravação do corpus do gensim.

In [13]:
corpora.MmCorpus.serialize('corpus.mm', corpus)

Criação de uma transformação (modelo *tfidf*) no gensim (https://radimrehurek.com/gensim/auto_examples/core/run_topics_and_transformations.html#sphx-glr-auto-examples-core-run-topics-and-transformations-py)

In [14]:
tfidf = models.TfidfModel(corpus)

Aplicamos a transformação a todo o corpus.

In [15]:
corpus_tfidf = tfidf[corpus]
for doc in corpus_tfidf:
    print(doc)

[(0, 0.03125409486507823), (1, 0.07273661615538123), (2, 0.1646821895837342), (3, 0.032892326598314876), (4, 0.040184170201418866), (5, 0.04832554911685889), (6, 0.08860253814199044), (7, 0.10918378164128584), (8, 0.042476483362151), (9, 0.08774618025935725), (10, 0.21403434050323675), (11, 0.1646821895837342), (12, 0.08060624578458077), (13, 0.004969810359240076), (14, 0.08039021361933052), (15, 0.10416192399727377), (16, 0.09134397732223937), (17, 0.1697040472277463), (18, 0.10683819838562957), (19, 0.12429346020303667), (20, 0.31327305089351143), (21, 0.21403434050323675), (22, 0.1455901714574619), (23, 0.1359964258476207), (24, 0.19494232237696443), (25, 0.11610597616894269), (26, 0.11533003866423167), (27, 0.10980277308106924), (28, 0.07024506914318802), (29, 0.1329328314174809), (30, 0.01762114927500252), (31, 0.08239835478881712), (32, 0.09511362115902558), (33, 0.09948223174560283), (34, 0.0025936914061225596), (35, 0.21403434050323675), (36, 0.0662341124749273), (37, 0.1697040

[(0, 0.019444685226424344), (13, 0.004328743413708392), (19, 0.07732897784384772), (20, 0.09745116425291647), (28, 0.04370285762854985), (34, 0.008875135322695862), (47, 0.00340761691444563), (55, 0.030661033363417106), (60, 0.02787171216148242), (75, 0.0433362889846379), (86, 0.037415624029610635), (124, 0.047759893936598484), (132, 0.07575343806873677), (141, 0.04426784607716923), (144, 0.05605044684881533), (150, 0.03491211800236556), (155, 0.10281723395791105), (218, 0.3055384986483933), (294, 0.08460995923706861), (295, 0.08793710031632275), (296, 0.04495144107109685), (297, 0.0787718725853525), (298, 0.059874330843786454), (299, 0.05494448695625467), (300, 0.050421059682665574), (301, 0.07605903171746672), (302, 0.1212830546618591), (303, 0.10940498606300306), (304, 0.06792851544767135), (305, 0.15465795568769544), (306, 0.06870757826880891), (307, 0.06060365072531426), (308, 0.06755187543663853), (309, 0.08019168858263373), (310, 0.063877655542884), (311, 0.049617642363681415), 

[(0, 0.04079074677443136), (3, 0.085857713741882), (4, 0.034963787798106494), (13, 0.004324175264198089), (30, 0.022997941263505007), (34, 0.011847891751532495), (46, 0.031714764722778954), (47, 0.00635417222605625), (78, 0.030856727418682228), (81, 0.047322341779998264), (83, 0.029098068131766176), (110, 0.020878505975519965), (135, 0.02980661988076312), (140, 0.11214988652162357), (158, 0.040164147054371324), (165, 0.019310948041874693), (194, 0.03323361045283369), (207, 0.047236411269325124), (318, 0.01131300176650221), (326, 0.013317147805031552), (356, 0.05029319034039395), (376, 0.01591447389926076), (382, 0.03615289550802032), (400, 0.030303389152899943), (459, 0.03323361045283369), (465, 0.09940833726644643), (513, 0.0162237257089344), (516, 0.0521856550472463), (546, 0.05847954860645912), (558, 0.05017367508638058), (559, 0.08480854473657375), (560, 0.032914049047292525), (561, 0.029155539908783144), (562, 0.04623726257887105), (563, 0.025809534623187618), (564, 0.071644046671

[(0, 0.03007322978422962), (1, 0.034994214051167545), (3, 0.06329912929485025), (13, 0.007651259756530336), (19, 0.11959731374398146), (20, 0.03767959240780131), (28, 0.03379550927121216), (30, 0.016955374119679713), (34, 0.004367465654316677), (47, 0.007905351407706651), (56, 0.06031839552215773), (60, 0.021553252072527944), (78, 0.0341239690651988), (95, 0.03600989701654881), (123, 0.049631270168781084), (126, 0.04248868424382058), (132, 0.03905352582566944), (135, 0.03296267167118585), (149, 0.028162356722724054), (161, 0.03365301717879457), (286, 0.03476104140339276), (326, 0.029454448203113038), (328, 0.06395513295688199), (332, 0.049631270168781084), (336, 0.03192787205735503), (349, 0.03787305039709272), (446, 0.08789275233455998), (457, 0.031084301319026165), (539, 0.042351360352621215), (649, 0.043343925292822494), (724, 0.05011320098470615), (770, 0.060859353771595036), (771, 0.09378843445670115), (772, 0.0402113870356631), (773, 0.09378843445670115), (774, 0.0937884344567011

[(0, 0.06299947758531275), (1, 0.04887219673554465), (3, 0.044201128443165955), (4, 0.08100000146596291), (13, 0.002671397845577776), (30, 0.023679525377827484), (34, 0.0008713589067748734), (47, 0.003680150178504191), (165, 0.029824892518952508), (193, 0.048399992239655444), (296, 0.048546552630529614), (326, 0.020567737072400723), (474, 0.055209109719956836), (618, 0.09263797295968339), (721, 0.043907445202384175), (969, 0.0978229656302804), (970, 0.10532689317074666), (971, 0.11065101449019062), (972, 0.11815494203065686), (973, 0.11815494203065686), (974, 0.11065101449019062), (975, 0.11815494203065686), (976, 0.11815494203065686), (977, 0.11065101449019062), (978, 0.11815494203065686), (979, 0.07068552052319053), (980, 0.09031903808981413), (981, 0.11815494203065686), (982, 0.07749098922990391), (983, 0.11815494203065686), (984, 0.11815494203065686), (985, 0.09249884431083644), (986, 0.11815494203065686), (987, 0.11815494203065686), (988, 0.09031903808981413), (989, 0.118154942030

...

[(0, 0.024899931345411318), (3, 0.026205099767711255), (4, 0.016007231748465297), (13, 0.008710713332566723), (30, 0.007019326732527804), (34, 0.0077489131691104345), (47, 0.007272717988928277), (78, 0.028253848790194252), (88, 0.0345144613289329), (132, 0.016167703283492325), (138, 0.06560060741078717), (145, 0.04869877413571388), (162, 0.062444146585792136), (198, 0.010065163714129615), (219, 0.03246036774725102), (325, 0.02603098659694262), (326, 0.024387594659323556), (330, 0.04149255909560919), (376, 0.02914405879950631), (399, 0.023915309809847508), (416, 0.025080431850880595), (418, 0.17183090482384306), (421, 0.03246036774725102), (424, 0.01870225931706956), (427, 0.03920770431847331), (450, 0.054173727977813904), (465, 0.01820457556306052), (530, 0.022936761024609596), (547, 0.03997676727841977), (562, 0.08467395830090399), (563, 0.02363240529996451), (632, 0.021935358723458847), (800, 0.051344815226596674), (851, 0.030504620019338638), (876, 0.05295335523449859), (992, 0.0321

[(4, 0.045012471617163395), (13, 0.0033401727090546685), (14, 0.09004944461214852), (34, 0.007263336546243403), (47, 0.010225472373999138), (55, 0.055204013388968624), (71, 0.08840666575642359), (81, 0.121845812503486), (144, 0.20183335516613732), (157, 0.09362325985085578), (318, 0.029128775970158352), (325, 0.07319935537723314), (424, 0.05259091202744251), (521, 0.05443455990818974), (577, 0.10304534814188211), (691, 0.12834208652428206), (721, 0.07319935537723314), (752, 0.06275823982112361), (861, 0.12671784385744891), (966, 0.117841849211504), (1231, 0.09766593844279914), (1377, 0.0727833470233472), (1482, 0.10493879403797476), (1622, 0.11667742854998327), (1910, 0.10695608005169203), (1970, 0.08075448252273922), (2043, 0.1755934705025085), (2756, 0.22894534088434207), (2779, 0.07306006175245695), (3007, 0.07659001986155864), (3089, 0.10196265861552599), (3242, 0.06623094744022417), (3710, 0.15057344684921833), (4934, 0.16870871418153882), (5197, 0.1755934705025085), (5243, 0.1073

[(13, 0.004404327862696542), (31, 0.05215912876290372), (34, 0.008209185994666477), (46, 0.046146610424650215), (47, 0.005778529197087659), (58, 0.11131531310200954), (60, 0.028358381803164235), (78, 0.044898122108622145), (81, 0.06885643609820795), (86, 0.07613788098039188), (91, 0.09106954084497351), (94, 0.06709958419421486), (95, 0.015793168239787013), (101, 0.033102061766034786), (124, 0.048593832315920835), (144, 0.05702914707096084), (161, 0.04427847392928337), (166, 0.03406113815588739), (167, 0.03480319273571283), (185, 0.046146610424650215), (297, 0.0400736564941409), (326, 0.019377133555869827), (375, 0.08240302723093869), (399, 0.03800376041089021), (521, 0.030761580712879273), (544, 0.07252755345381337), (563, 0.03755419754516782), (567, 0.08608733882200571), (577, 0.05823208269341304), (582, 0.09487746231338469), (590, 0.06593572432228884), (649, 0.05702914707096084), (674, 0.04014706986958534), (691, 0.07252755345381337), (707, 0.05554436525256838), (715, 0.0659357243222

[(0, 0.07188110949393016), (13, 0.002286007540060048), (34, 0.0014913039136295486), (47, 0.004198975738758153), (55, 0.05667227498745455), (60, 0.05151663733132167), (83, 0.1538291097984304), (88, 0.099636329895594), (91, 0.08271975002320119), (231, 0.08498314810055409), (318, 0.02990351426439312), (325, 0.07514623923469906), (326, 0.035201048100951406), (332, 0.11862878682873643), (356, 0.08862623529910417), (615, 0.23930145021572954), (830, 0.08784598153040539), (838, 0.09319568996993588), (931, 0.12417821794479401), (1164, 0.14822218720409253), (1427, 0.18439599633819587), (1770, 0.06293072883638011), (1808, 0.1373597222720137), (2062, 0.10090346270024998), (2067, 0.13839831026431715), (2289, 0.10467456028596907), (2737, 0.22879860138890998), (3228, 0.09123077504939481), (3244, 0.10155655998028779), (3576, 0.17319586124125225), (3836, 0.17319586124125225), (4501, 0.1309109094406491), (4701, 0.13443388087252908), (6496, 0.3250768147085443), (6498, 0.24443674094842024), (6792, 0.12626

[(0, 0.021128937524105242), (3, 0.022236443471437595), (4, 0.02716600257691275), (5, 0.03266987933952555), (13, 0.003359777752014312), (14, 0.05434679226657736), (30, 0.011912556218368307), (31, 0.055704370833252644), (34, 0.00701372974176324), (36, 0.04477673823185907), (47, 0.004937035428310768), (78, 0.04794983549330501), (81, 0.0367682948473506), (95, 0.016866625672757266), (101, 0.03535200007542808), (140, 0.08713770155108579), (144, 0.06090540298679739), (157, 0.056503667250245485), (165, 0.030008262680086772), (166, 0.03637626463169811), (167, 0.037168756463396575), (327, 0.028974574528162465), (337, 0.08264708379636808), (399, 0.04058686586981368), (411, 0.07635748300513101), (424, 0.031739755679511115), (516, 0.02703131303884165), (521, 0.032852437149332954), (563, 0.040106746336013674), (590, 0.07041735791837296), (691, 0.077457231917822), (694, 0.09426930355598356), (709, 0.10597446664851252), (789, 0.06612483508991329), (805, 0.06696501132014389), (966, 0.07112011103445424)

Podemos usar várias transformações, inclusive as encadeando. Abaixo, rodamos um modelo do tipo [LSI](https://en.wikipedia.org/wiki/Latent_semantic_indexing) e mostramos os tópicos identificados. 

In [23]:
lsi = models.LsiModel(corpus_tfidf, id2word=dicionario, num_topics=100)  # incializa uma transf. LSI com 100 tópicos
corpus_lsi = lsi[corpus_tfidf]
lsi.print_topics(num_topics=10, num_words=5)

[(0, '0.211*"q" + 0.171*"Excelência" + 0.124*"–" + 0.104*"amigo" + 0.102*"V"'),
 (1, '0.619*"q" + 0.223*"pa" + 0.178*"pr" + 0.162*"Exa" + 0.153*"V"'),
 (2,
  '0.445*"Excelência" + -0.231*"q" + -0.184*"di" + -0.138*"Adelmário" + -0.131*"i"'),
 (3,
  '0.295*"di" + 0.237*"compadre" + 0.201*"i" + -0.190*"–" + 0.175*"Pitanga"'),
 (4,
  '0.485*"Excelência" + 0.207*"q" + 0.143*"–" + 0.137*"di" + 0.122*"Adelmário"'),
 (5, '-0.360*"V" + -0.328*"Exa" + 0.304*"“" + 0.298*"”" + 0.203*"q"'),
 (6,
  '-0.397*"compadre" + 0.318*"di" + -0.249*"senhor" + 0.241*"i" + 0.171*"u"'),
 (7,
  '0.319*"Excelência" + -0.226*"Exa" + 0.222*"q" + -0.180*"“" + -0.179*"”"'),
 (8, '0.321*"V" + 0.286*"”" + 0.285*"“" + 0.269*"Exa" + 0.129*"Exca"'),
 (9,
  '0.244*"compadre" + -0.235*"Zenilta" + -0.187*"Oliveira" + -0.180*"Comadre" + 0.180*"senhor"')]

O próximo passo é buscas por similaridade (https://radimrehurek.com/gensim/auto_examples/core/run_similarity_queries.html#sphx-glr-auto-examples-core-run-similarity-queries-py)

## Whoosh: Indexação

In [ ]:
schema = Schema(id=ID(unique=True), 
                de=TEXT(stored=True),
                para=TEXT(stored=True), 
                data=DATETIME(stored=True), 
                texto=TEXT(stored=True))

if os.path.exists('index_cartas'):
    ix = open_dir('index_cartas')
else:
    os.mkdir('index_cartas')
    ix = create_in('index_cartas', schema)

In [ ]:
writer = ix.writer()

for i in cartas.index:
    
    if pd.isna(cartas.loc[i, 'de']):
        cartas.loc[i, 'de'] = ''
        
    if pd.isna(cartas.loc[i, 'para']):
        cartas.loc[i, 'para'] = '' 
    
    if pd.isna(cartas.loc[i, 'data']):
        writer.add_document(id=cartas.loc[i, 'id'], 
                            de=cartas.loc[i, 'de'], 
                            para=cartas.loc[i, 'para'], 
                            texto=cartas.loc[i, 'texto'])
    else:
        writer.add_document(id=cartas.loc[i, 'id'], 
                            de=cartas.loc[i, 'de'], 
                            para=cartas.loc[i, 'para'], 
                            data=cartas.loc[i, 'data'], 
                            texto=cartas.loc[i, 'texto'])
writer.commit()

### Whoosh: Buscas

In [ ]:
searcher = ix.searcher()
termos = [x.decode('utf-8') for x in list(searcher.lexicon("texto"))]
termos[0:len(termos):500]

In [ ]:
qp = QueryParser("texto", schema=ix.schema)
q = qp.parse('de:"Benicio Penalva"')
print(q)

with ix.searcher() as s:
    results = s.search(q)
    print(results[:10])

In [ ]:
q = qp.parse('de:"Benicio Penalva" AND texto:(política OR partido)')
print(q)

with ix.searcher() as s:
    results = s.search(q)
    for i in results[:10]:
        print(i)